In [3]:
from tqdm import tqdm
import itertools
import statsmodels.api as sm
import warnings
warnings.filterwarnings('ignore')
from matplotlib import gridspec
import matplotlib.dates as mdates
from matplotlib.dates import DateFormatter
import datetime
from scipy.stats import norm, describe

import seaborn as sns
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np

In [4]:
data_path = "../Datasets/VNP46A2_regional/NCR_NTL_VNP46A2.csv"


In [ ]:
data = pd.read_csv(data_path, parse_dates=True, index_col = 0)
data.head()


Size of original dataset: 4142


In [ ]:
n_init = len(data)
print("Size of original dataset: %d" % n_init)

Size of original dataset: 4142


In [8]:
data.describe()

DNB_BRDF_Corrected_NTL  DNB_Lunar_Irradiance  \
count             2670.000000           4107.000000   
mean                22.044298             26.312285   
std                  7.017390             36.803359   
min                  0.032562              0.500000   
25%                 18.622556              0.500000   
50%                 22.592008              0.500000   
75%                 26.418989             44.950000   
max                 73.589233            164.198530   

       Gap_Filled_DNB_BRDF_Corrected_NTL  Latest_High_Quality_Retrieval  \
count                        4107.000000                    4107.000000   
mean                           23.818935                       3.993595   
std                             3.226065                       4.479393   
min                             4.203769                       0.003160   
25%                            22.083439                       1.072860   
50%                            24.217076                       2.373474   
75%                            25.753041                       5.256165   
max                            35.925257                      28.598642   

       Mandatory_Quality_Flag  QF_Cloud_Mask    Snow_Flag  
count             2670.000000    4107.000000  4083.000000  
mean                 0.447146     371.321069     0.000673  
std                  0.698937     294.696914     0.012084  
min                  0.000000       3.080248     0.000000  
25%                  0.013410      61.538253     0.000000  
50%                  0.049517     297.811024     0.000000  
75%                  0.600256     728.083553     0.000000  
max                  2.000000     753.366582     0.369491

In [ ]:
# Assume 'data' is a DataFrame with a datetime index and NTL columns
NTL = data['DNB_BRDF_Corrected_NTL']
NTL_GF = data['Gap_Filled_DNB_BRDF_Corrected_NTL']

# Step 1: Generate full date range
full_index = pd.date_range(start=NTL.index.min(), end=NTL.index.max(), freq='D')

# Step 2: Find missing dates in original NTL (raw) data
missing_dates = full_index.difference(NTL.index)
missing_days = len(missing_dates)

# Step 3: Convert to a DataFrame for plotting
missing_df = pd.DataFrame(index=missing_dates)
missing_df['missing'] = 0

# Step 4: Create plot
fig = go.Figure()

fig.add_trace(go.Scatter(
    x=NTL.index, 
    y=NTL, 
    mode='lines+markers',
    line=dict(color='blue', width=1),
    marker=dict(size=2),
    name=f"DNB_BRDF_Corrected_NTL ({NTL.count()} observations)"
))

fig.add_trace(go.Scatter(
    x=NTL_GF.index, 
    y=NTL_GF, 
    mode='lines',
    line=dict(color='red', width=1.5),
    name=f"Gap_Filled_DNB_BRDF_Corrected_NTL ({NTL_GF.count()} observations)"
))

fig.add_trace(go.Scatter(
    x=missing_df.index, 
    y=missing_df['missing'], 
    mode='markers',
    marker=dict(color='orange', symbol='x', size=8),
    name=f"No sensor data record ({missing_days} observations)"
))

fig.update_layout(
    title='National Capital Region (NCR) VNP46A2 Nighttime Lights (NTL)',
    xaxis_title='Date',
    yaxis_title='NTL Radiance (nW·cm⁻²·sr⁻¹)',
    template='plotly_white',
    height=450,
    xaxis=dict(
        rangeselector=dict(
            buttons=list([
                dict(count=6, label='6m', step='month', stepmode='backward'),
                dict(count=1, label='1y', step='year', stepmode='backward'),
                dict(step='all')
            ])
        ),
        rangeslider=dict(visible=True),
        type='date'
    ),
    legend=dict(x=0.01, y=0.99, borderwidth=0.5)
)

fig.show()

In [33]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from matplotlib import cm

# Assume 'y' is your NTL series and 'decomposition' is from statsmodels seasonal_decompose

# Normalize seasonal and residuals for color mapping
seasonal = decomposition.seasonal
residual = decomposition.resid

seasonal_norm = (seasonal - seasonal.min()) / (seasonal.max() - seasonal.min())
residual_norm = (residual - residual.min()) / (residual.max() - residual.min())

# Convert colormap from matplotlib to hex for Plotly
seasonal_colors = [f"rgb{tuple(int(c*255) for c in cm.viridis(s)[:3])}" for s in seasonal_norm]
residual_colors = [f"rgb{tuple(int(c*255) for c in cm.gnuplot2(r)[:3])}" for r in residual_norm]

fig = make_subplots(rows=3, cols=1, shared_xaxes=True,
                    row_heights=[0.75, 0.5, 0.5],
                    vertical_spacing=0.03,
                    subplot_titles=["Trend", "Seasonality", "Residuals"])

# --- Trend subplot ---
fig.add_trace(go.Scatter(x=decomposition.trend.index, y=y,
                         mode='lines', name='Observed (yₜ)',
                         line=dict(color='red', width=1)),
              row=1, col=1)

fig.add_trace(go.Scatter(x=decomposition.trend.index, y=decomposition.trend,
                         mode='lines', name='Trend (Tₜ)',
                         line=dict(color='black', width=3)),
              row=1, col=1)

# --- Seasonality subplot ---
fig.add_trace(go.Scatter(x=seasonal.index, y=seasonal,
                         mode='markers',
                         marker=dict(color=seasonal_colors, size=3),
                         name='Seasonality (Sₜ)'),
              row=2, col=1)

# --- Residuals subplot ---
fig.add_trace(go.Scatter(x=residual.index, y=residual,
                         mode='markers',
                         marker=dict(color=residual_colors, size=2),
                         name='Residuals (Eₜ)'),
              row=3, col=1)

# --- Layout & Axis Titles ---
fig.update_layout(
    height=700,
    width=900,
    template='plotly_white',
    title_text='Seasonal Decomposition of NTL Radiance (Additive)',
    showlegend=True
)

fig.update_yaxes(title_text="Trend, Tₜ / Observed, yₜ", row=1, col=1)
fig.update_yaxes(title_text="Seasonality, Sₜ", row=2, col=1)
fig.update_yaxes(title_text="Residuals, Eₜ", row=3, col=1)
fig.update_xaxes(title_text="Date", row=3, col=1)

# ✅ Attach range slider only to the bottom x-axis
fig.update_layout(
    xaxis3=dict(
        title="Date",
        rangeslider=dict(visible=True),
        type="date"
    )
)

fig.show()

In [44]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
from matplotlib import cm
import pandas as pd
from statsmodels.tsa.seasonal import seasonal_decompose

# Define STL periods to explore
rolling_options = [30, 60, 90, 120, 180, 365]
slider_steps = []
trace_refs = []

# COVID-19 markers
covid_events = [
    {"name": "Lockdown Start", "date": "2020-03-16"},
    {"name": "Delta Surge", "date": "2021-08-01"},
    {"name": "Omicron Surge", "date": "2022-01-01"},
]

# Initialize figure
fig = make_subplots(rows=3, cols=1, shared_xaxes=True,
                    row_heights=[0.75, 0.25, 0.25],
                    vertical_spacing=0.03,
                    subplot_titles=["Trend", "Seasonality", "Residuals"])

# Decomposition and traces for each rolling window
for i, period in enumerate(rolling_options):
    decomposition = seasonal_decompose(y, model='additive', period=period)
    seasonal = decomposition.seasonal
    residual = decomposition.resid
    trend = decomposition.trend

    seasonal_norm = (seasonal - seasonal.min()) / (seasonal.max() - seasonal.min())
    residual_norm = (residual - residual.min()) / (residual.max() - residual.min())
    seasonal_colors = [f"rgb{tuple(int(c*255) for c in cm.viridis(s)[:3])}" for s in seasonal_norm]
    residual_colors = [f"rgb{tuple(int(c*255) for c in cm.gnuplot2(r)[:3])}" for r in residual_norm]

    show = (i == 0)

    # Trend subplot
    fig.add_trace(go.Scatter(x=y.index, y=y, name=f"Observed ({period})",
                             line=dict(color='red', width=1), visible=show), row=1, col=1)
    trace_refs.append((period, len(fig.data) - 1))

    fig.add_trace(go.Scatter(x=trend.index, y=trend, name=f"Trend ({period})",
                             line=dict(color='black', width=3), visible=show), row=1, col=1)
    trace_refs.append((period, len(fig.data) - 1))

    # Seasonality line with small dots
    fig.add_trace(go.Scatter(x=seasonal.index, y=seasonal, mode='lines+markers',
                             line=dict(color='green', width=1.5),
                             marker=dict(color=seasonal_colors, size=2),
                             name=f"Seasonality ({period})", visible=show), row=2, col=1)
    trace_refs.append((period, len(fig.data) - 1))

    # Residuals line with small dots
    fig.add_trace(go.Scatter(x=residual.index, y=residual, mode='lines+markers',
                             line=dict(color='gray', width=1.5),
                             marker=dict(color=residual_colors, size=1.5),
                             name=f"Residuals ({period})", visible=show), row=3, col=1)
    trace_refs.append((period, len(fig.data) - 1))

# Slider steps
for period in rolling_options:
    vis = [False] * len(fig.data)
    for (p, idx) in trace_refs:
        if p == period:
            vis[idx] = True
    slider_steps.append(dict(
        method='update',
        label=f"{period}d",
        args=[{"visible": vis},
              {"title": f"STL Decomposition (Period = {period} days)"}]
    ))

# COVID markers
for event in covid_events:
    fig.add_vline(x=pd.to_datetime(event["date"]), line_dash="dash", line_color="blue")
    fig.add_annotation(
        x=event["date"], y=1, yref='paper',
        text=event["name"], showarrow=False,
        font=dict(color="blue"), bgcolor="white",
        bordercolor="blue", borderwidth=1, borderpad=2,
        xanchor="left"
    )

# Layout
fig.update_layout(
    sliders=[dict(
        active=0,
        currentvalue={"prefix": "Rolling Period: "},
        pad={"t": 60},
        steps=slider_steps
    )],
    height=800,
    width=1000,
    template='plotly_white',
    title='STL Decomposition of NTL Radiance (Interactive)',
    showlegend=True
)

fig.update_layout(
    sliders=[dict(
        active=0,
        currentvalue={"prefix": "Rolling Period: "},
        pad={"t": 50},  # top padding
        y=1.4,          # position above the plot
        x=0.6,
        xanchor="left",
        len=0.4
    )],
    height=800,
    width=1200,
    template='plotly_white',
    title='STL Decomposition of NTL Radiance (Interactive)',
    showlegend=True
)

fig.update_xaxes(
    title_text="Date",
    row=3,
    col=1,
    rangeslider=dict(visible=True),
    type="date"
)
fig.update_yaxes(title_text="Trend / Observed", row=1, col=1)
fig.update_yaxes(title_text="Seasonality", row=2, col=1)
fig.update_yaxes(title_text="Residuals", row=3, col=1)

fig.show()